# Landsat-8


<div class="alert-info">

### Overview
    
* **teaching:** 30 minutes
* **exercises:** 0
* **questions:**
    * How can I find, anaylize, and visualize Landsat8 satellite imagery for an area of interest using Python?
    
</div>


This notebook will focus on accessing public datasets on AWS for a target area affected by Cyclone Kenneth (2019-04-25). Read more about this event and its impact at the [Humanitarian Open Street Map website](https://tasks.hotosm.org/project/5977). We will use a bounding box we will work with covers the island of Nagazidja, including the captial [city of Moroni](https://en.wikipedia.org/wiki/Moroni,_Comoros) - Union of the Comoros, a sovereign archipelago nation in the Indian Ocean. 

We will examine raster images from the [Landsat-8 instrument](https://www.usgs.gov/land-resources/nli/landsat). The Landsat program is the longest-running civilian satellite imagery program, with the first satellite launched in 1972 by the US Geological Survey. Landsat 8 is the latest satellite in this program, and was launched in 2013. Landsat observations are processed into “scenes”, each of which is approximately 183 km x 170 km, with a spatial resolution of 30 meters and a temporal resolution of 16 days. The duration of the landsat program makes it an attractive source of medium-scale imagery for land surface change analyses.

Additional code examples for Landsat-8 can be found in Geohackweek 2018 content: https://geohackweek.github.io/raster/04-workingwithrasters/

## Table of contents

1. [**Sat-search**](#Sat-search)
1. [**Holoviz visualization**](#Holoviz)
1. [**Rasterio and xarray**](#Rasterio-and-xarray)

In [1]:
# Import libraries
import geopandas as gpd
import pandas as pd
import satsearch
from satstac import Items

import holoviews as hv
import hvplot.xarray
import hvplot.pandas
import geoviews as gv

import ipywidgets
import datetime

from ipywidgets import interact
from IPython.display import display, Image

import json
from cartopy import crs as ccrs

import rasterio
import rasterio.mask
from rasterio.session import AWSSession
import xarray as xr

import matplotlib.pyplot as plt
from matplotlib.colors import LogNorm
%matplotlib inline

In [2]:
# Set up our bounding box
bbox = [43.16, -11.32, 43.54, -11.96]
west, north, east, south = bbox
bbox_ctr = [0.5*(north+south), 0.5*(west+east)]

## Sat-search 

[Sat-search](https://github.com/sat-utils/sat-search) is open-source software designed to easily discover public imagery on AWS. It depends upon metadata called Spatio-Temporal Asset Catalogs [STAC catalogs](https://stacspec.org/) to filter scenes. We will use it to search for Landsat-8 data covering our area of interest

In [3]:
# bbox as a python list is great for use in python, but we can instead save to a more interoperable format (GeoJSON)
# Here is a great website for creating and visualizing geojson on a map: http://geojson.io

aoi = { "type": "Polygon", 
    "coordinates": [[[west, south], [west, north], [east, north], [east, south], [west, south]]]
}
# pretty print formatting
print(json.dumps(aoi, sort_keys=False, indent=2))

# save to file for future use
with open('aoi-5977.geojson', 'w') as f:
    json.dump(aoi, f)

{
  "type": "Polygon",
  "coordinates": [
    [
      [
        43.16,
        -11.96
      ],
      [
        43.16,
        -11.32
      ],
      [
        43.54,
        -11.32
      ],
      [
        43.54,
        -11.96
      ],
      [
        43.16,
        -11.96
      ]
    ]
  ]
}


In [4]:
# Load results to pandas geodataframe
# now other packages such as geojson can read this file
gfa = gpd.read_file('aoi-5977.geojson')
gfa

geometry
0  POLYGON ((43.16 -11.96, 43.16 -11.32, 43.54 -1...

In [5]:
# Get results for bbox and time range
results = satsearch.Search(bbox=bbox, datetime='2019-02-01/2019-06-01')
print('%s items' % results.found())
items = results.items()
print('%s collections:' % len(items._collections))
print(items._collections)


137 items
2 collections:
[landsat-8-l1, sentinel-2-l1c]


In [6]:
# If you are unfamiliar with one of these satellites, we can look at stored metadata
col = items._collections[1]

print('Title:', col.title)
print('Collection Version:', col.version)
print('Keywords: ', col.keywords)
print('License:', col.license)
print('Providers:', col.providers)
print('Extent', col.extent)

Title: Sentinel 2 L1C
Collection Version: 0.1.0
Keywords:  ['sentinel', 'earth observation', 'esa']
License: proprietary
Providers: [{'roles': ['producer'], 'name': 'ESA', 'url': 'https://earth.esa.int/web/guest/home'}, {'roles': ['processor'], 'name': 'Sinergise', 'url': 'https://registry.opendata.aws/sentinel-2/'}, {'roles': ['host'], 'name': 'AWS', 'url': 'http://sentinel-pds.s3-website.eu-central-1.amazonaws.com/'}, {'roles': ['processor'], 'name': 'Development Seed', 'url': 'https://github.com/sat-utils/sat-stac-sentinel'}]
Extent {'spatial': [-180, -90, 180, 90], 'temporal': ['2013-06-01', None]}


In [7]:
# We can delve deeper to see what kind of metadata is available at the scene level
for key in col.properties:
    if key == 'eo:bands':
        [print(band) for band in col[key]]
    else:
        print('%s: %s' % (key, col[key]))

collection: sentinel-2-l1c
eo:gsd: 10
eo:instrument: MSI
eo:off_nadir: 0
{'full_width_half_max': 0.027, 'center_wavelength': 0.4439, 'name': 'B01', 'gsd': 60, 'common_name': 'coastal'}
{'full_width_half_max': 0.098, 'center_wavelength': 0.4966, 'name': 'B02', 'gsd': 10, 'common_name': 'blue'}
{'full_width_half_max': 0.045, 'center_wavelength': 0.56, 'name': 'B03', 'gsd': 10, 'common_name': 'green'}
{'full_width_half_max': 0.038, 'center_wavelength': 0.6645, 'name': 'B04', 'gsd': 10, 'common_name': 'red'}
{'full_width_half_max': 0.019, 'center_wavelength': 0.7039, 'name': 'B05', 'gsd': 20}
{'full_width_half_max': 0.018, 'center_wavelength': 0.7402, 'name': 'B06', 'gsd': 20}
{'full_width_half_max': 0.028, 'center_wavelength': 0.7825, 'name': 'B07', 'gsd': 20}
{'full_width_half_max': 0.145, 'center_wavelength': 0.8351, 'name': 'B08', 'gsd': 10, 'common_name': 'nir'}
{'full_width_half_max': 0.033, 'center_wavelength': 0.8648, 'name': 'B8A', 'gsd': 20}
{'full_width_half_max': 0.026, 'center

In [8]:
# Search for just tier1 Landsat8 scenes, all dates
properties =  ["landsat:tier=T1"] 

bbox = (west, south, east, north) #(min lon, min lat, max lon, max lat)

results = satsearch.Search.search(collection='landsat-8-l1', 
                        bbox=bbox, 
                        sort=['<datetime'], #earliest scene first
                        property=properties)
print('%s items' % results.found())

307 items


In [9]:
# Save search results for later or to share with others
items = results.items()
items.save('items-landsat8.json')
items = Items.load('items-landsat8.json')

In [10]:
# # Assets correspond to actual images related to a STAC metadata item
# Use pandas to better display python dictionaries!
pd.DataFrame(items[0].assets).T.reset_index()

index             type                    title  \
0       index        text/html          HTML index page   
1   thumbnail       image/jpeg          Thumbnail image   
2          B1  image/x.geotiff         Band 1 (coastal)   
3          B2  image/x.geotiff            Band 2 (blue)   
4          B3  image/x.geotiff           Band 3 (green)   
5          B4  image/x.geotiff             Band 4 (red)   
6          B5  image/x.geotiff             Band 5 (nir)   
7          B6  image/x.geotiff          Band 6 (swir16)   
8          B7  image/x.geotiff          Band 7 (swir22)   
9          B8  image/x.geotiff             Band 8 (pan)   
10         B9  image/x.geotiff          Band 9 (cirrus)   
11        B10  image/x.geotiff           Band 10 (lwir)   
12        B11  image/x.geotiff           Band 11 (lwir)   
13        ANG       text/plain  Angle coefficients file   
14        MTL       text/plain   original metadata file   
15        BQA  image/x.geotiff        Band quality data   

                                                 href eo:bands  
0   https://s3-us-west-2.amazonaws.com/landsat-pds...      NaN  
1   https://s3-us-west-2.amazonaws.com/landsat-pds...      NaN  
2   https://s3-us-west-2.amazonaws.com/landsat-pds...      [0]  
3   https://s3-us-west-2.amazonaws.com/landsat-pds...      [1]  
4   https://s3-us-west-2.amazonaws.com/landsat-pds...      [2]  
5   https://s3-us-west-2.amazonaws.com/landsat-pds...      [3]  
6   https://s3-us-west-2.amazonaws.com/landsat-pds...      [4]  
7   https://s3-us-west-2.amazonaws.com/landsat-pds...      [5]  
8   https://s3-us-west-2.amazonaws.com/landsat-pds...      [6]  
9   https://s3-us-west-2.amazonaws.com/landsat-pds...      [7]  
10  https://s3-us-west-2.amazonaws.com/landsat-pds...      [8]  
11  https://s3-us-west-2.amazonaws.com/landsat-pds...      [9]  
12  https://s3-us-west-2.amazonaws.com/landsat-pds...     [10]  
13  https://s3-us-west-2.amazonaws.com/landsat-pds...      NaN  
14  https://s3-us-west-2.amazonaws.com/landsat-pds...      NaN  
15  https://s3-us-west-2.amazonaws.com/landsat-pds...      NaN

In [12]:
# Read results into a geopandas GeoDataFrame
# adds additional spatial column (?)
gfl = gpd.read_file('items-landsat8.json')
gfl = gfl.sort_values('datetime').reset_index(drop=True)
print('records:', len(gfl))
gfl.head()

records: 307


id    collection             datetime  eo:sun_azimuth  \
0  LC81620682013117LGN02  landsat-8-l1  2013-04-27T07:10:38       47.708602   
1  LC81630682013140LGN02  landsat-8-l1  2013-05-20T07:17:05       40.523393   
2  LC81630682013188LGN01  landsat-8-l1  2013-07-07T07:17:03       40.086481   
3  LC81620682013197LGN01  landsat-8-l1  2013-07-16T07:10:52       41.584821   
4  LC81620692013197LGN01  landsat-8-l1  2013-07-16T07:11:16       40.824820   

   eo:sun_elevation  eo:cloud_cover eo:row eo:column  \
0         52.660185              11    068       162   
1         48.563416              10    068       163   
2         45.396038               3    068       163   
3         46.105807              20    068       162   
4         44.878648              12    069       162   

                         landsat:product_id       landsat:scene_id  \
0  LC08_L1TP_162068_20130427_20170505_01_T1  LC81620682013117LGN02   
1  LC08_L1TP_163068_20130520_20170504_01_T1  LC81630682013140LGN02   
2  LC08_L1TP_163068_20130707_20170503_01_T1  LC81630682013188LGN01   
3  LC08_L1TP_162068_20130716_20170503_01_T1  LC81620682013197LGN01   
4  LC08_L1TP_162069_20130716_20170503_01_T1  LC81620692013197LGN01   

  landsat:processing_level landsat:tier  eo:epsg eo:instrument  eo:off_nadir  \
0                     L1TP           T1    32738      OLI_TIRS             0   
1                     L1TP           T1    32738      OLI_TIRS             0   
2                     L1TP           T1    32738      OLI_TIRS             0   
3                     L1TP           T1    32738      OLI_TIRS             0   
4                     L1TP           T1    32738      OLI_TIRS             0   

  eo:platform                                           eo:bands  eo:gsd  \
0   landsat-8  [ { "full_width_half_max": 0.02, "center_wavel...      15   
1   landsat-8  [ { "full_width_half_max": 0.02, "center_wavel...      15   
2   landsat-8  [ { "full_width_half_max": 0.02, "center_wavel...      15   
3   landsat-8  [ { "full_width_half_max": 0.02, "center_wavel...      15   
4   landsat-8  [ { "full_width_half_max": 0.02, "center_wavel...      15   

  landsat:revision                                           geometry  
0             None  POLYGON ((43.52213129803964 -10.57931517918585...  
1             None  POLYGON ((41.91608063019623 -10.57711060325962...  
2             None  POLYGON ((41.95988647195887 -10.51730062777292...  
3             None  POLYGON ((43.51964136276217 -10.5188928854251,...  
4             None  POLYGON ((43.19541393649787 -11.96321353597531...

In [13]:
# Hack for neat display of band information
import ast
band_info = pd.DataFrame(ast.literal_eval(gfl.iloc[0]['eo:bands']))
band_info

full_width_half_max  center_wavelength name  gsd common_name
0                  0.02               0.44   B1   30     coastal
1                  0.06               0.48   B2   30        blue
2                  0.06               0.56   B3   30       green
3                  0.04               0.65   B4   30         red
4                  0.03               0.86   B5   30         nir
5                  0.08               1.60   B6   30      swir16
6                  0.20               2.20   B7   30      swir22
7                  0.18               0.59   B8   15         pan
8                  0.02               1.37   B9   30      cirrus
9                  0.80              10.90  B10  100      lwir11
10                 1.00              12.00  B11  100      lwir12

In [14]:
# Note the cloud_cover column, we can narrow our search by any of these properties
# the following is filter to reduce cloud cover
properties.extend(["eo:cloud_cover<10"])

test = satsearch.Search.search(collection='landsat-8-l1', 
                        bbox=bbox, 
                        sort=['<datetime'], #earliest scene first
                        property=properties)
print('%s items' % test.found())

132 items


In [15]:
# Or since we can just use geopandas to filter results
subset = gfl[gfl['eo:cloud_cover'] < 10]
print('%s items' % len(subset))

132 items


## Holoviz

[Holoviz](https://holoviz.org/) is a set of Python visualization libraries that simplify interactive visualizations of data in a web-browser. We'll use several of these libraries including hvplot and geoviews to visualize both vector data (such as image footprints) and raster data (actual raster values). 

<div class="alert-warning">

#### Note 
    
the toolbars on the right and side of these plots. We are using a library called Bokeh that gives interactive widgets to zoom in and pan around on maps.
</div>

In [16]:
# plotting tools

# Plot search AOI and frames on a map using Holoviz Libraries
cols = gfl.loc[:,('id','geometry')]

footprints = cols.hvplot(geo=True, line_color='k', alpha=0.1, title='Landsat 8 T1')
aoi = gfa.hvplot(geo=True, line_color='b', fill_color=None)
tiles = gv.tile_sources.CartoEco.options(width=700, height=500) 
labels = gv.tile_sources.StamenLabels.options(level='annotation')
tiles * footprints * aoi * labels

:Overlay
   .WMTS.I      :WMTS   [Longitude,Latitude]
   .Polygons.I  :Polygons   [Longitude,Latitude]   (id)
   .Polygons.II :Polygons   [Longitude,Latitude]
   .WMTS.II     :WMTS   [Longitude,Latitude]

## ipywidgets

[ipywidgets](https://ipywidgets.readthedocs.io/en/latest/) provide another convenient approach to custom visualizations. The function below allows us to browse through all the image thumbnails for a group of images (more specifically a specific Landsat8 path and row). 

In [17]:
def browse_images(items):
    n = len(items)

    def view_image(i=0):
        item = items[i]
        print(f"id={item.id}\tdate={item.datetime}\tcloud%={item['eo:cloud_cover']}")
        display(Image(item.asset('thumbnail')['href']))
    
    interact(view_image, i=(0,n-1))

In [18]:
# Custom syntax (additional fields, query strings instead of query dict)
properties =  ["eo:row=068",
               "eo:column=162",
               "landsat:tier=T1"] 
results = satsearch.Search.search(collection='landsat-8-l1', 
                        bbox=bbox, 
                        sort=['<datetime'], #earliest scene first
                        property=properties)
print('%s items' % results.found())
items = results.items()

115 items


In [19]:
# May not work on Chrome currently, does work on Safari
browse_images(items) 

interactive(children=(IntSlider(value=0, description='i', max=114), Output()), _dom_classes=('widget-interact'…

## Rasterio and xarray

To actually load full resolution data from a particular Landsat-8 band we'll use rasterio and xarray libraries.

In [20]:
# These are environmnent variable settings for efficiently reading data on AWS S3
# configure settings
env = rasterio.Env(GDAL_DISABLE_READDIR_ON_OPEN='EMPTY_DIR',
                  CPL_VSIL_CURL_ALLOWED_EXTENSIONS='TIF',
                 )

In [22]:
# block size relates to ability to parallelize computations

item = items[0] # pick first item from our search
band = 'red'
url = item.asset(band)['href']
print(url)
with env:
    with rasterio.open(url) as src:
        print(src.profile) # image metadata # gets object back 
        width = src.width
        blockx = src.profile['blockxsize'] # how image is pre-chunked into blocks
        blocky = src.profile['blockysize']
        xchunk = int(width/blockx)*blockx
        ychunk = blocky
        # data array - python object, incl. metadata and crs about raster
        # like a pandas equivalent, which includes data and metadata
        da = xr.open_rasterio(src, chunks={'band': 1, 'x': xchunk, 'y': ychunk})
da

In [24]:
da.data

dask.array<open_rasterio-6d8b45772b6ec09cad6566e7b1b8f9f6<this-array>, shape=(1, 7291, 7521), dtype=uint16, chunksize=(1, 512, 7168)>

In [26]:
# side note - often end up with lots of zeros in remote sensing data

# This will pull raster data over network. if operating in the same AWS region, should be very fast!
# NOTE: seems there is a bug currently with 'logz' for a log-scale colorbar
img = da.hvplot.image(rasterize=True, logz=True, width=700, height=500, cmap='reds', title=f'{item.id} ({band})')
img 

:DynamicMap   [band]
   :Image   [x,y]   (value)

### Visualize with on-the-fly reprojection

In [27]:
# Display image in latitute, longitude coordinates instead of EPSG:32638 (UTM 38N)
crs = ccrs.UTM(zone='38N') 
img = da.hvplot.image(crs=crs, rasterize=True, width=700, height=500, cmap='reds', alpha=0.8, title=f'{item.id} ({band})') # , logz=True not working 
aoi = gfa.hvplot(geo=True, line_color='b', fill_color=None)
img * aoi

:DynamicMap   [band]
   :Overlay
      .Image.I    :Image   [x,y]   (value)
      .Polygons.I :Polygons   [Longitude,Latitude]

### Image subsets and crop by shapefile

Often we are only interested in small regions of full images. One of the killer features of cloud-optimized data formats stored on the cloud is that we can efficiently pull subsets of an image rather than the whole thing. Here we'll pull only the pixels within a vector polygon in our area of interest.

<div class="alert-warning">

#### Note 
    
It's up to you to make sure the vector and raster CRS's match!

</div>

In [28]:
# this is a quite useful piece of code to subset image by polygon
# takes a polygon, and gets raster pixel data that is in our polygon

with rasterio.open(url) as src:
    # re-project vector to match raster CRS
    print(src.meta)
    shape = gfa.to_crs(epsg=src.crs.to_epsg()) # identify shape to use, use utm crs
    
    # use raster io image to subset image
    out_image, out_transform = rasterio.mask.mask(src, shape.geometry.values, crop=True)
    out_meta = src.meta
    out_meta.update({
                 "height": out_image.shape[1],
                 "width": out_image.shape[2],
                 "transform": out_transform})
    print(out_meta)
    
    # write small image to local Geotiff file
    with rasterio.open('subset.tif', 'w', **out_meta) as dst:
        dst.write(out_image)

{'driver': 'GTiff', 'dtype': 'uint16', 'nodata': None, 'width': 7521, 'height': 7291, 'count': 1, 'crs': CRS.from_epsg(32638), 'transform': Affine(30.0, 0.0, 301185.0,
       0.0, -30.0, -1169985.0)}
{'driver': 'GTiff', 'dtype': 'uint16', 'nodata': None, 'width': 1329, 'height': 2369, 'count': 1, 'crs': CRS.from_epsg(32638), 'transform': Affine(30.0, 0.0, 301185.0,
       0.0, -30.0, -1251735.0)}


In [ ]:
# Plot just the subset
import rasterio.plot
with rasterio.open('subset.tif') as src:
    rasterio.plot.show(src, cmap='Reds')

In [ ]:
# Excercise 1) Load and visualize the highest-resolution 15m pancromatic band instead of the red band
# Excercise 2) Calculate a band ratio between any two bands

# Xarray DataArray

The xarray multidimensional data model works well if you want to perform computations on multiple bands for a single image, and to utilize dask for distributed computations

In [ ]:
# Use just 30 meter bands for simplicity
bands = band_info.query('gsd == 30').common_name.to_list()
bands

In [ ]:
def load_dataarray(item, bands):
    ''' Load STAC item into an xarray DataSet '''
    data_arrays = []
    for band in bands:
        url = item.asset(band)['href']
        da = xr.open_rasterio(url, chunks={'band': 1, 'x': 1024, 'y': 1024})
        data_arrays.append(da.assign_coords(band=[band]))
    return xr.concat(data_arrays, dim='band')

In [ ]:
from dask.distributed import Client

client = Client("tcp://192.168.52.168:39175")
client

In [ ]:
da = load_dataarray(item, bands)

In [ ]:
img = da.hvplot.image(groupby='band', rasterize=True, width=700, height=500, alpha=0.8, title=f'{item.id}') # , logz=True not working 
img

In [ ]:
# some images have a cloud mask band, depends on the data set

# Xarray DataSets

It is arguable better to think of image bands as observational variables rather than a dimension of the dataset. DataSets are meant for storing multiple variables. This data structure is also useful for timeseries of multiple images.

In [ ]:
# xarray is used for multidimensional data, the concept of a datacube

In [29]:
bands = band_info.query('gsd == 30').common_name.to_list()
bands

['coastal', 'blue', 'green', 'red', 'nir', 'swir16', 'swir22', 'cirrus']

In [30]:
def load_dataset(item, bands):
    ''' Load STAC item into an xarray DataSet '''
    data_arrays = []
    for band in bands:
        url = item.asset(band)['href']
        da = xr.open_rasterio(url, chunks={'band': 1, 'x': 1024, 'y': 1024})
        da = da.expand_dims(time=[pd.to_datetime(item.date)])
        ds = da.to_dataset(name=band)
        data_arrays.append(ds)
    ds = xr.combine_by_coords(data_arrays)
    return ds

In [31]:
# ds = load_dataset(item, bands)

In [32]:
print(ds)
print('Dataset size (Gb): ', ds.nbytes/1e9)

<xarray.Dataset>
Dimensions:  (band: 1, time: 1, x: 7521, y: 7291)
Coordinates:
  * time     (time) datetime64[ns] 2013-04-27
  * band     (band) int64 1
  * y        (y) float64 -1.17e+06 -1.17e+06 -1.17e+06 ... -1.389e+06 -1.389e+06
  * x        (x) float64 3.012e+05 3.012e+05 3.013e+05 ... 5.268e+05 5.268e+05
Data variables:
    blue     (time, band, y, x) uint16 dask.array<shape=(1, 1, 7291, 7521), chunksize=(1, 1, 1024, 1024)>
    cirrus   (time, band, y, x) uint16 dask.array<shape=(1, 1, 7291, 7521), chunksize=(1, 1, 1024, 1024)>
    coastal  (time, band, y, x) uint16 dask.array<shape=(1, 1, 7291, 7521), chunksize=(1, 1, 1024, 1024)>
    green    (time, band, y, x) uint16 dask.array<shape=(1, 1, 7291, 7521), chunksize=(1, 1, 1024, 1024)>
    nir      (time, band, y, x) uint16 dask.array<shape=(1, 1, 7291, 7521), chunksize=(1, 1, 1024, 1024)>
    red      (time, band, y, x) uint16 dask.array<shape=(1, 1, 7291, 7521), chunksize=(1, 1, 1024, 1024)>
    swir16   (time, band, y, x) ui

In [ ]:
ds['blue'].hvplot.image(rasterize=True, logz=True, width=700, height=500, cmap='blues', title=f'{item.id} (blue)')

In [ ]:
# Lazy computation with dask
NDVI = (ds['nir'] - ds['red']) / (ds['nir'] + ds['red'])
NDVI

In [ ]:
# Compute and store in local memory
ndvi = NDVI.compute()
ndvi

In [ ]:
# Put together a larger dataset
results = satsearch.Search.search(collection='landsat-8-l1', 
                        bbox=bbox, 
                        datetime='2019-08-15/2019-09-30',
                        sort=['<datetime']) #earliest scene first
print('%s items' % results.found())
items = results.items()
items.save('set.geojson')

In [ ]:
gf = gpd.read_file('set.geojson')
gf

In [ ]:
# Plot search AOI and frames on a map using Holoviz Libraries
cols = gf.loc[:,('id','geometry')]

footprints = cols.hvplot(geo=True, line_color='k', alpha=0.1, title='Landsat 8 T1')
tiles = gv.tile_sources.CartoEco.options(width=700, height=500) 
labels = gv.tile_sources.StamenLabels.options(level='annotation')
tiles * footprints * labels

In [ ]:
# NOTE: this is not a very efficient bit of code, but it works
datasets = []
for item in items:
    datasets.append(load_dataset(item, bands))
DS = xr.concat(datasets, dim='band')

In [ ]:
DS = DS.assign_coords(band=range(len(datasets)))

In [ ]:
DS

In [ ]:
# gfa is a polygon representation of our bounding box - the blue box in this tutorial
bounds = gfa.to_crs(epsg=32638).bounds #32638 UTM 38N    #32738 UTM 38S
bounds

In [ ]:
print(bounds.minx[0], bounds.maxx[0], bounds.miny[0], bounds.maxy[0])

In [ ]:
mosaic = DS.sel(x=slice(bounds.minx[0], bounds.maxx[0]), y=slice(bounds.miny[0], bounds.maxy[0])).mean(dim='band')

In [ ]:
# Can change chunks before computing at dask
mosaic.chunk(chunks=dict(time=3,x=1395,y=2368))

In [ ]:
mosaic['nir'].hvplot.image(x='x',y='y',groupby='time', rasterize=True, width=700, height=500)